In [1]:
#insert all packages needed
from rdkit import Chem
from rdkit.Chem import Descriptors
from rdkit.ML.Descriptors import MoleculeDescriptors
from rdkit.Chem import Draw
from rdkit.Chem.Draw import IPythonConsole
import pandas as pd 
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.preprocessing import MinMaxScaler

In [2]:
#import the smiles list
file_name = 'tested_molecules-1.csv'


In [3]:
#split the csv file into multiple columns
#read the dataframe
df = pd.read_csv(file_name)

#split the dataframe
new_columns = df['SMILES;ALDH1_inhibition'].str.split(';', expand=True)
df_molecules = pd.concat([df, new_columns], axis=1)

#drop the original column
df_molecules = df_molecules.drop('SMILES;ALDH1_inhibition', axis=1)

#rename the column names 
df_molecules = df_molecules.rename(columns={0:'SMILES',1:'ALDH1-inhibitor'})


df_molecules

SMILES ALDH1-inhibitor
0    COc1ccccc1CC(NC(C)=O)C(=O)NC1CCN(c2nnnn2-c2ccc...               1
1               O=C(CSc1nc2cccnc2n1Cc1ccccc1)NCc1ccco1               1
2    Cc1cccc2cc(C[NH+](CC3CCCO3)C(c3nnnn3Cc3ccco3)C...               1
3                    CCN(CC)c1ccc2c(Cl)c(Br)c(=O)oc2c1               1
4    CS(=O)(=O)N1CCc2cc(-c3csc(NC(=O)Cc4cccs4)n3)ccc21               1
..                                                 ...             ...
995             COc1ccc(N2C(=O)CC([NH2+]C3CC3)C2=O)cc1               0
996                       CCNc1oc(COc2cccc(C)c2)nc1C#N               0
997                          NC(=O)Cn1cnc(-c2ccccc2)c1               0
998  Cc1cc(NC(=O)CSc2nc3c(c(=O)n(C)c(=O)n3C)n2C(C)C...               0
999          O=C(Cn1nnc2c(cnn2-c2ccccc2)c1=O)NCc1cccs1               0

[1000 rows x 2 columns]

In [4]:
#since the list is very large, to try stuff out, we look at the first 4 smiles
only_smiles_list = df_molecules['SMILES']

smiles_tryout = only_smiles_list
smiles_tryout

0      COc1ccccc1CC(NC(C)=O)C(=O)NC1CCN(c2nnnn2-c2ccc...
1                 O=C(CSc1nc2cccnc2n1Cc1ccccc1)NCc1ccco1
2      Cc1cccc2cc(C[NH+](CC3CCCO3)C(c3nnnn3Cc3ccco3)C...
3                      CCN(CC)c1ccc2c(Cl)c(Br)c(=O)oc2c1
4      CS(=O)(=O)N1CCc2cc(-c3csc(NC(=O)Cc4cccs4)n3)ccc21
                             ...                        
995               COc1ccc(N2C(=O)CC([NH2+]C3CC3)C2=O)cc1
996                         CCNc1oc(COc2cccc(C)c2)nc1C#N
997                            NC(=O)Cn1cnc(-c2ccccc2)c1
998    Cc1cc(NC(=O)CSc2nc3c(c(=O)n(C)c(=O)n3C)n2C(C)C...
999            O=C(Cn1nnc2c(cnn2-c2ccccc2)c1=O)NCc1cccs1
Name: SMILES, Length: 1000, dtype: object

In [5]:
#draw the four mole images
mols = [Chem.MolFromSmiles(smi) for smi in smiles_tryout]
#Draw.MolsToGridImage(mols, molsPerRow=2, subImgSize=(200, 200))

In [6]:
#calculate descriptor list
desc_list = [n[0] for n in Descriptors._descList]

phc_desc = [i for i in desc_list if not i.startswith('fr_')]
print(len(phc_desc))
print(phc_desc)        

124
['MaxAbsEStateIndex', 'MaxEStateIndex', 'MinAbsEStateIndex', 'MinEStateIndex', 'qed', 'MolWt', 'HeavyAtomMolWt', 'ExactMolWt', 'NumValenceElectrons', 'NumRadicalElectrons', 'MaxPartialCharge', 'MinPartialCharge', 'MaxAbsPartialCharge', 'MinAbsPartialCharge', 'FpDensityMorgan1', 'FpDensityMorgan2', 'FpDensityMorgan3', 'BCUT2D_MWHI', 'BCUT2D_MWLOW', 'BCUT2D_CHGHI', 'BCUT2D_CHGLO', 'BCUT2D_LOGPHI', 'BCUT2D_LOGPLOW', 'BCUT2D_MRHI', 'BCUT2D_MRLOW', 'AvgIpc', 'BalabanJ', 'BertzCT', 'Chi0', 'Chi0n', 'Chi0v', 'Chi1', 'Chi1n', 'Chi1v', 'Chi2n', 'Chi2v', 'Chi3n', 'Chi3v', 'Chi4n', 'Chi4v', 'HallKierAlpha', 'Ipc', 'Kappa1', 'Kappa2', 'Kappa3', 'LabuteASA', 'PEOE_VSA1', 'PEOE_VSA10', 'PEOE_VSA11', 'PEOE_VSA12', 'PEOE_VSA13', 'PEOE_VSA14', 'PEOE_VSA2', 'PEOE_VSA3', 'PEOE_VSA4', 'PEOE_VSA5', 'PEOE_VSA6', 'PEOE_VSA7', 'PEOE_VSA8', 'PEOE_VSA9', 'SMR_VSA1', 'SMR_VSA10', 'SMR_VSA2', 'SMR_VSA3', 'SMR_VSA4', 'SMR_VSA5', 'SMR_VSA6', 'SMR_VSA7', 'SMR_VSA8', 'SMR_VSA9', 'SlogP_VSA1', 'SlogP_VSA10', 'Slog

In [7]:
#calculate molecular descriptors
calc = MoleculeDescriptors.MolecularDescriptorCalculator(desc_list)

rdkit_desc1 = [calc.CalcDescriptors(m) for m in mols]
rdkit_desc_data = [calc.CalcDescriptors(m) for m in mols]

rdkit_desc = []
for element in rdkit_desc_data:   
    tuple_floats = tuple(float(x) for x in element)
    rdkit_desc.append(tuple_floats)

#print(len(rdkit_desc[0]))
print(rdkit_desc1[0])


(13.083531447323905, 13.083531447323905, 0.001173180692030762, -0.6831399723499987, 0.5203647862499531, 463.54200000000026, 434.3100000000002, 463.2331877880001, 178, 0, 0.2498683330982345, -0.4964765338733181, 0.4964765338733181, 0.2498683330982345, 1.088235294117647, 1.7941176470588236, 2.5, 16.465857064612035, 10.012387123815586, 2.277377408380586, -2.329164203915786, 2.2133733533282376, -2.5243684910679804, 5.869761700770313, -0.12818123363075157, 3.3456496356368177, 1.3746473471677294, 1110.519071976258, 23.915638315627202, 19.34719971591, 19.34719971591, 16.546045193307766, 11.32986098667514, 11.32986098667514, 8.265228811036, 8.265228811036, 5.888539678818338, 5.888539678818338, 4.187622471031995, 4.187622471031995, -3.95, 69581108.14936109, 23.21634357240783, 10.778357860560856, 5.506758970272485, 197.8337076591357, 20.270349892663187, 11.791352662431866, 0.0, 17.762698739689505, 0.0, 0.0, 9.589074368143644, 0.0, 4.681802935145185, 0.0, 41.4968842190707, 47.030966134243585, 32.

In [8]:
#add columns to dataframe
#add columns to dataframe
for col in range(len(desc_list)):
    column = []
    for row in range(len(rdkit_desc)):
        #the row iteration is for the molecule and the col iteration for the descriptor, this makes a list which will be
        #added to the dataframe
        descriptor = rdkit_desc[row][col]
        column.append(descriptor)
    df_molecules[desc_list[col]] = column
df_molecules = df_molecules.drop(columns=['fr_Al_COO', 'fr_Al_OH', 'fr_Al_OH_noTert', 'fr_ArN', 'fr_Ar_COO', 'fr_Ar_N', 'fr_Ar_NH', 'fr_Ar_OH', 'fr_COO', 'fr_COO2', 'fr_C_O', 'fr_C_O_noCOO', 'fr_C_S', 'fr_HOCCN', 'fr_Imine', 'fr_NH0', 'fr_NH1', 'fr_NH2', 'fr_N_O', 'fr_Ndealkylation1', 'fr_Ndealkylation2', 'fr_Nhpyrrole', 'fr_SH', 'fr_aldehyde', 'fr_alkyl_carbamate', 'fr_alkyl_halide', 'fr_allylic_oxid', 'fr_amide', 'fr_amidine', 'fr_aniline', 'fr_aryl_methyl', 'fr_azide', 'fr_azo', 'fr_barbitur', 'fr_benzene', 'fr_benzodiazepine', 'fr_bicyclic', 'fr_diazo', 'fr_dihydropyridine', 'fr_epoxide', 'fr_ester', 'fr_ether', 'fr_furan', 'fr_guanido', 'fr_halogen', 'fr_hdrzine', 'fr_hdrzone', 'fr_imidazole', 'fr_imide', 'fr_isocyan', 'fr_isothiocyan', 'fr_ketone', 'fr_ketone_Topliss', 'fr_lactam', 'fr_lactone', 'fr_methoxy', 'fr_morpholine', 'fr_nitrile', 'fr_nitro', 'fr_nitro_arom', 'fr_nitro_arom_nonortho', 'fr_nitroso', 'fr_oxazole', 'fr_oxime', 'fr_para_hydroxylation', 'fr_phenol', 'fr_phenol_noOrthoHbond', 'fr_phos_acid', 'fr_phos_ester', 'fr_piperdine', 'fr_piperzine', 'fr_priamide', 'fr_prisulfonamd', 'fr_pyridine', 'fr_quatN', 'fr_sulfide', 'fr_sulfonamd', 'fr_sulfone', 'fr_term_acetylene', 'fr_tetrazole', 'fr_thiazole', 'fr_thiocyan', 'fr_thiophene', 'fr_unbrch_alkane', 'fr_urea'])

pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 100)
df_molecules
 

C:\Users\20213656\AppData\Local\Temp\ipykernel_11432\499668220.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_molecules[desc_list[col]] = column
C:\Users\20213656\AppData\Local\Temp\ipykernel_11432\499668220.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_molecules[desc_list[col]] = column
C:\Users\20213656\AppData\Local\Temp\ipykernel_11432\499668220.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider 

SMILES ALDH1-inhibitor  \
0    COc1ccccc1CC(NC(C)=O)C(=O)NC1CCN(c2nnnn2-c2ccc...               1   
1               O=C(CSc1nc2cccnc2n1Cc1ccccc1)NCc1ccco1               1   
2    Cc1cccc2cc(C[NH+](CC3CCCO3)C(c3nnnn3Cc3ccco3)C...               1   
3                    CCN(CC)c1ccc2c(Cl)c(Br)c(=O)oc2c1               1   
4    CS(=O)(=O)N1CCc2cc(-c3csc(NC(=O)Cc4cccs4)n3)ccc21               1   
..                                                 ...             ...   
995             COc1ccc(N2C(=O)CC([NH2+]C3CC3)C2=O)cc1               0   
996                       CCNc1oc(COc2cccc(C)c2)nc1C#N               0   
997                          NC(=O)Cn1cnc(-c2ccccc2)c1               0   
998  Cc1cc(NC(=O)CSc2nc3c(c(=O)n(C)c(=O)n3C)n2C(C)C...               0   
999          O=C(Cn1nnc2c(cnn2-c2ccccc2)c1=O)NCc1cccs1               0   

     MaxAbsEStateIndex  MaxEStateIndex  MinAbsEStateIndex  MinEStateIndex  \
0            13.083531       13.083531           0.001173       -0.683140   
1            12.170097       12.170097           0.066966       -0.066966   
2            10.905837       10.905837           0.016881       -0.016881   
3            11.562446       11.562446           0.270607       -0.454447   
4            12.108866       12.108866           0.086947       -3.251317   
..                 ...             ...                ...             ...   
995          12.276695       12.276695           0.095308       -0.234165   
996           8.926724        8.926724           0.197944        0.197944   
997          10.688087       10.688087           0.166502       -0.368508   
998          12.603109       12.603109           0.065686       -0.447592   
999          12.570699       12.570699           0.190808       -0.399579   

          qed    MolWt  HeavyAtomMolWt  ExactMolWt  NumValenceElectrons  \
0    0.520365  463.542         434.310  463.233188                178.0   
1    0.498564  378.457         360.313  378.115047                136.0   
2    0.382043  477.589         444.325  477.260865                184.0   
3    0.795948  330.609         317.505  328.981818                 96.0   
4    0.687618  419.553         402.417  419.043204                140.0   
..        ...      ...             ...         ...                  ...   
995  0.779148  261.301         244.165  261.123369                100.0   
996  0.891297  257.293         242.173  257.116427                 98.0   
997  0.805927  201.229         190.141  201.090212                 76.0   
998  0.644831  392.441         372.281  392.126674                144.0   
999  0.575368  366.406         352.294  366.089895                130.0   

     NumRadicalElectrons  MaxPartialCharge  MinPartialCharge  \
0                    0.0          0.249868         -0.496477   
1                    0.0          0.230353         -0.467476   
2                    0.0          0.219930         -0.492903   
3                    0.0          0.351723         -0.421732   
4                    0.0          0.231765         -0.301646   
..                   ...               ...               ...   
995                  0.0          0.292020         -0.496766   
996                  0.0          0.235725         -0.483868   
997                  0.0          0.236896         -0.368122   
998                  0.0          0.331704         -0.359541   
999                  0.0          0.280885         -0.349596   

     MaxAbsPartialCharge  MinAbsPartialCharge  FpDensityMorgan1  \
0               0.496477             0.249868          1.088235   
1               0.467476             0.230353          1.111111   
2               0.492903             0.219930          1.228571   
3               0.421732             0.351723          1.333333   
4               0.301646             0.231765          1.296296   
..                   ...                  ...               ...   
995             0.496766             0.292020          1.210526   
996             0.483868    

In [9]:
#put all the column names of the dataframe in a list
columns = []
for column in df_molecules:
    columns.append(column)

In [10]:
#check the correlations between all columns and put the highest correlations in a list
highcorr=[]
allcorr = []
for column1 in range(len(columns)):
    for column2 in range(len(columns)):
        if column1 != column2 and column1>1 and column2>1 and column2>=column1:
            corr = df_molecules[columns[column1]].corr(df_molecules[columns[column2]])
            #print("Correlation between ", columns[column1], " and ", columns[column2], "is: ", round(corr, 2))
            allcorr.append(corr)
            if corr >= 0.80 or corr <= -0.80:
                #all correlations of 0,9 or higher are put in a list
                highcorr.append([columns[column1],columns[column2],round(corr,2)])
print(highcorr)
print(len(highcorr))

[['MaxAbsEStateIndex', 'MaxEStateIndex', 1.0], ['MinEStateIndex', 'VSA_EState1', -0.83], ['MolWt', 'HeavyAtomMolWt', 1.0], ['MolWt', 'ExactMolWt', 1.0], ['MolWt', 'NumValenceElectrons', 0.96], ['MolWt', 'BertzCT', 0.84], ['MolWt', 'Chi0', 0.97], ['MolWt', 'Chi0n', 0.92], ['MolWt', 'Chi0v', 0.97], ['MolWt', 'Chi1', 0.95], ['MolWt', 'Chi1n', 0.89], ['MolWt', 'Chi1v', 0.93], ['MolWt', 'Chi2n', 0.81], ['MolWt', 'Chi2v', 0.86], ['MolWt', 'Chi3v', 0.8], ['MolWt', 'Kappa1', 0.95], ['MolWt', 'Kappa2', 0.83], ['MolWt', 'LabuteASA', 0.98], ['MolWt', 'HeavyAtomCount', 0.96], ['MolWt', 'MolMR', 0.95], ['HeavyAtomMolWt', 'ExactMolWt', 1.0], ['HeavyAtomMolWt', 'NumValenceElectrons', 0.95], ['HeavyAtomMolWt', 'BertzCT', 0.85], ['HeavyAtomMolWt', 'Chi0', 0.96], ['HeavyAtomMolWt', 'Chi0n', 0.9], ['HeavyAtomMolWt', 'Chi0v', 0.95], ['HeavyAtomMolWt', 'Chi1', 0.94], ['HeavyAtomMolWt', 'Chi1n', 0.86], ['HeavyAtomMolWt', 'Chi1v', 0.92], ['HeavyAtomMolWt', 'Chi2v', 0.84], ['HeavyAtomMolWt', 'Kappa1', 0.94], 

In [11]:
#put all the columns with high correlation in a list (except the first ones to have the high correlation like MolWt)
dupe_col = []
for i in range(len(highcorr)):
    if highcorr[i][1] not in dupe_col:
        dupe_col.append(highcorr[i][1])
print(len(dupe_col))

40


In [12]:
descriptors = ['MaxAbsEStateIndex', 'MinAbsEStateIndex',
       'MinEStateIndex', 'qed', 'MolWt', 'NumRadicalElectrons',
       'MaxPartialCharge', 'MinPartialCharge', 'FpDensityMorgan1',
       'BCUT2D_MWHI', 'BCUT2D_MWLOW', 'BCUT2D_CHGHI', 'BCUT2D_CHGLO',
       'BCUT2D_LOGPHI', 'BCUT2D_LOGPLOW', 'BCUT2D_MRHI', 'BCUT2D_MRLOW',
       'AvgIpc', 'BalabanJ', 'HallKierAlpha', 'Ipc', 'PEOE_VSA1', 'PEOE_VSA10',
       'PEOE_VSA11', 'PEOE_VSA12', 'PEOE_VSA13', 'PEOE_VSA14', 'PEOE_VSA2',
       'PEOE_VSA3', 'PEOE_VSA4', 'PEOE_VSA5', 'PEOE_VSA6', 'PEOE_VSA7',
       'PEOE_VSA8', 'PEOE_VSA9', 'SMR_VSA1', 'SMR_VSA10', 'SMR_VSA2',
       'SMR_VSA3', 'SMR_VSA4', 'SMR_VSA5', 'SMR_VSA6', 'SMR_VSA7', 'SMR_VSA8',
       'SMR_VSA9', 'SlogP_VSA1', 'SlogP_VSA10', 'SlogP_VSA11', 'SlogP_VSA12',
       'SlogP_VSA2', 'SlogP_VSA3', 'SlogP_VSA4', 'SlogP_VSA7', 'SlogP_VSA8',
       'SlogP_VSA9', 'TPSA', 'EState_VSA1', 'EState_VSA10', 'EState_VSA11',
       'EState_VSA2', 'EState_VSA3', 'EState_VSA4', 'EState_VSA5',
       'EState_VSA6', 'EState_VSA7', 'EState_VSA8', 'EState_VSA9',
       'VSA_EState2', 'VSA_EState3', 'VSA_EState4', 'VSA_EState5',
       'VSA_EState7', 'VSA_EState8', 'VSA_EState9', 'FractionCSP3',
       'NHOHCount', 'NumAliphaticCarbocycles', 'NumAliphaticHeterocycles',
       'NumAliphaticRings', 'NumAromaticHeterocycles', 'NumAromaticRings',
       'NumSaturatedHeterocycles', 'RingCount','MolLogP']
for i in dupe_col:    
    df_molecules = df_molecules.drop(columns = [i])
print(df_molecules)

columns_new = []
for descriptor in df_molecules:
    columns_new.append(descriptor)
print(columns_new)

                                                SMILES ALDH1-inhibitor  \
0    COc1ccccc1CC(NC(C)=O)C(=O)NC1CCN(c2nnnn2-c2ccc...               1   
1               O=C(CSc1nc2cccnc2n1Cc1ccccc1)NCc1ccco1               1   
2    Cc1cccc2cc(C[NH+](CC3CCCO3)C(c3nnnn3Cc3ccco3)C...               1   
3                    CCN(CC)c1ccc2c(Cl)c(Br)c(=O)oc2c1               1   
4    CS(=O)(=O)N1CCc2cc(-c3csc(NC(=O)Cc4cccs4)n3)ccc21               1   
..                                                 ...             ...   
995             COc1ccc(N2C(=O)CC([NH2+]C3CC3)C2=O)cc1               0   
996                       CCNc1oc(COc2cccc(C)c2)nc1C#N               0   
997                          NC(=O)Cn1cnc(-c2ccccc2)c1               0   
998  Cc1cc(NC(=O)CSc2nc3c(c(=O)n(C)c(=O)n3C)n2C(C)C...               0   
999          O=C(Cn1nnc2c(cnn2-c2ccccc2)c1=O)NCc1cccs1               0   

     MaxAbsEStateIndex  MinAbsEStateIndex  MinEStateIndex       qed    MolWt  \
0            13.083531         

# Remove Outliers

In [13]:
def find_outliers(df, column):
    q1=df[column].quantile(0.25)
    q3=df[column].quantile(0.75)
    IQR=q3-q1
    lower_outliers = df[column][(df[column]<(q1-IQR))]
    upper_outliers = df[column][(df[column]>(q3+IQR))]
    frames = [lower_outliers, upper_outliers]
    outliers = pd.concat(frames)
    print(outliers)
    return outliers

#outliers = find_outliers(df_molecules_1, 'MaxAbsEStateIndex')  
#outliers

In [14]:
descriptors = ['MaxAbsEStateIndex', 'MinAbsEStateIndex',
       'MinEStateIndex', 'qed', 'MolWt', 'NumRadicalElectrons',
       'MaxPartialCharge', 'MinPartialCharge', 'FpDensityMorgan1',
       'BCUT2D_MWHI', 'BCUT2D_MWLOW', 'BCUT2D_CHGHI', 'BCUT2D_CHGLO',
       'BCUT2D_LOGPHI', 'BCUT2D_LOGPLOW', 'BCUT2D_MRHI', 'BCUT2D_MRLOW',
       'AvgIpc', 'BalabanJ', 'HallKierAlpha', 'Ipc', 'PEOE_VSA1', 'PEOE_VSA10',
       'PEOE_VSA11', 'PEOE_VSA12', 'PEOE_VSA13', 'PEOE_VSA14', 'PEOE_VSA2',
       'PEOE_VSA3', 'PEOE_VSA4', 'PEOE_VSA5', 'PEOE_VSA6', 'PEOE_VSA7',
       'PEOE_VSA8', 'PEOE_VSA9', 'SMR_VSA1', 'SMR_VSA10', 'SMR_VSA2',
       'SMR_VSA3', 'SMR_VSA4', 'SMR_VSA5', 'SMR_VSA6', 'SMR_VSA7', 'SMR_VSA8',
       'SMR_VSA9', 'SlogP_VSA1', 'SlogP_VSA10', 'SlogP_VSA11', 'SlogP_VSA12',
       'SlogP_VSA2', 'SlogP_VSA3', 'SlogP_VSA4', 'SlogP_VSA7', 'SlogP_VSA8',
       'SlogP_VSA9', 'TPSA', 'EState_VSA1', 'EState_VSA10', 'EState_VSA11',
       'EState_VSA2', 'EState_VSA3', 'EState_VSA4', 'EState_VSA5',
       'EState_VSA6', 'EState_VSA7', 'EState_VSA8', 'EState_VSA9',
       'VSA_EState2', 'VSA_EState3', 'VSA_EState4', 'VSA_EState5',
       'VSA_EState7', 'VSA_EState8', 'VSA_EState9', 'FractionCSP3',
       'NHOHCount', 'NumAliphaticCarbocycles', 'NumAliphaticHeterocycles',
       'NumAliphaticRings', 'NumAromaticHeterocycles', 'NumAromaticRings',
       'NumSaturatedHeterocycles', 'RingCount','MolLogP']
def remove_outliers(df, column):
    outliers = find_outliers(df, column)
    df_outliers = pd.DataFrame.from_dict(outliers)
    list_indexes_outliers = list(df_outliers.index.values)
    df_column = df.filter([column], axis=1)
    for i in range(len(list_indexes_outliers)):
        index_to_drop = list_indexes_outliers[i]
#         df_column.drop(index_to_drop)
        df_column[column][index_to_drop] = 'NaN'
    return df_column

pd.set_option('display.max_rows', 1000)
for descriptor in descriptors:
    df_molecules[descriptor]=remove_outliers(df_molecules, descriptor)
    

13      6.011299
52      9.679179
85      5.728289
93     10.383623
98      5.396740
112     9.651783
128     9.345715
129     4.523711
133     4.354542
135     5.091186
142    10.372195
144    10.082781
160     5.338834
198     5.359724
202     5.419591
216     5.807513
220     5.322822
252     4.541634
268     5.558917
277     9.389074
288     5.268563
289     5.116451
290     8.400719
297    10.428982
301     5.363287
302     4.118715
303    10.466205
305    10.401183
306    10.336111
311     9.548955
312    10.159860
316     2.502315
317     9.415264
320     9.487593
323     8.391575
326    10.255484
328     8.706713
329     5.229316
332     5.510613
334     5.510603
337     5.281053
341     6.051410
347     5.933225
357     5.964657
362     6.059950
378     5.837037
404     9.347802
419    10.202779
434     5.557464
438     5.777637
439     6.142864
445     5.537205
459     9.394551
461     6.147929
464     5.441153
465     9.679852
469     5.604206
478    10.434480
481     5.4783

6      12.083478
26     12.124355
251    23.877221
294    12.062545
299    12.062545
319    24.011646
321    12.062545
346    12.186480
379    17.981224
380    12.000420
381    18.611925
386    12.580810
521    12.000420
533    12.062545
538    16.910451
574    12.186480
676    12.000420
691    17.251130
716    12.347974
729    12.124355
734    17.808464
772    17.069230
831    12.124355
843    23.427429
859    12.186480
865    12.062545
938    12.103705
953    12.103705
964    18.031534
988    12.103705
993    24.373527
Name: PEOE_VSA14, dtype: float64
28     23.517811
41     18.950711
75     19.283521
89     18.950711
99     19.475955
105    25.760438
121    25.757446
141    39.913620
143    29.397840
145    19.283521
154    19.808765
156    19.283521
158    20.685574
161    25.023174
177    23.201880
187    19.703393
207    18.950711
208    21.950130
211    19.170787
212    20.007537
231    20.228637
232    29.292467
238    19.703393
241    30.336970
251    23.972686
259    25.02317

9       5.261892
12      5.261892
36      5.261892
45     10.523783
52     10.523783
107     5.261892
109     5.261892
128     5.261892
131     5.261892
140     5.261892
149     5.261892
205     5.261892
224     5.261892
225     5.261892
290     5.261892
323     5.261892
328     5.261892
339     5.261892
342     5.261892
343     5.261892
352     5.409284
353     5.261892
390     5.261892
410     5.261892
522     5.261892
523     5.261892
565    10.523783
581     5.261892
602     5.261892
614     5.261892
618    10.523783
647     5.261892
653     5.261892
700     5.261892
736     5.261892
749     5.261892
772    10.523783
775     5.261892
863     5.261892
888     5.261892
899     5.261892
907     5.261892
913     5.261892
921     5.261892
925     5.261892
943    15.785675
948     5.409284
954     5.261892
973     5.261892
996     5.261892
Name: SMR_VSA2, dtype: float64
0      30.840832
2      25.191233
5      24.512471
14     29.931018
16     29.931018
35     29.716399
62     25.107165


39     32.675606
46     27.619031
77     23.684315
88     25.597761
90     23.611718
105    35.419753
157    25.874685
167    28.555676
198    31.165325
200    27.938743
220    26.428462
222    26.428462
276    32.675606
289    29.172610
291    38.198564
325    23.785040
334    24.425661
338    32.675606
345    23.818813
358    27.938743
367    27.938743
388    25.811529
494    44.893479
497    27.938743
530    24.053979
556    51.140623
570    24.229729
631    27.938743
639    29.552481
643    25.811529
673    34.802820
694    28.185858
818    23.364603
831    27.938743
880    27.055449
896    26.428462
953    32.675606
965    27.724975
988    37.513194
Name: EState_VSA9, dtype: float64
26     46.555306
28     51.422721
75     41.415712
87     45.081141
89     42.932622
141    55.126673
143    51.474491
156    54.081729
173    47.250321
192    48.909029
208    63.636560
214    43.388932
232    57.172417
241    44.931670
251    58.793126
259    46.009793
264    43.703637
282    59.7404

4     -3.251317
5     -3.540253
15    -3.594898
17    -4.006749
25    -2.190141
27    -3.664604
32    -3.740406
38    -3.836039
39    -3.747172
40    -1.785816
50    -3.784519
53    -3.696685
54    -3.509259
56    -2.343597
62    -2.419766
69    -3.472980
71    -3.628322
79    -2.150868
92    -5.818713
100   -2.685423
101   -3.458795
116   -3.577749
117   -3.535194
137   -4.112639
138   -3.769743
157   -3.126599
168   -1.783759
175   -7.679243
176   -3.891146
183   -3.450530
184   -7.786946
188   -3.999725
193   -1.700100
210   -7.847588
217   -7.650251
226   -4.027726
240   -3.839071
243   -3.684578
263   -2.233541
266   -2.260282
269   -3.559521
270   -3.685942
273   -7.835871
274   -3.619548
275   -2.756573
292   -3.742701
313   -1.703093
330   -3.126008
349   -3.486096
350   -3.860803
352   -3.551819
354   -2.768836
361   -3.814401
374   -3.085919
377   -3.052072
392   -3.949884
403   -7.766624
416   -2.609666
422   -3.824526
427   -3.616296
447   -3.665936
448   -3.160253
477   -3

In [15]:
df_molecules


SMILES ALDH1-inhibitor  \
0    COc1ccccc1CC(NC(C)=O)C(=O)NC1CCN(c2nnnn2-c2ccc...               1   
1               O=C(CSc1nc2cccnc2n1Cc1ccccc1)NCc1ccco1               1   
2    Cc1cccc2cc(C[NH+](CC3CCCO3)C(c3nnnn3Cc3ccco3)C...               1   
3                    CCN(CC)c1ccc2c(Cl)c(Br)c(=O)oc2c1               1   
4    CS(=O)(=O)N1CCc2cc(-c3csc(NC(=O)Cc4cccs4)n3)ccc21               1   
5    CC1CCCCN1S(=O)(=O)c1ccc(NC(=O)c2cccc(-n3cnnn3)...               1   
6         COCCN(C(=O)C(F)(F)F)C(C(=O)NC1CCCCC1)c1ccco1               1   
7        COc1ccccc1N1CCN(C(=O)CSc2nnc(-c3ccoc3C)o2)CC1               1   
8                 O=c1c2ccccc2nc(SCc2ccccc2)n1Cc1ccco1               1   
9             N#Cc1c(NC(=O)CSc2nnnn2C2CCCC2)sc2c1CCCC2               1   
10   COc1ccc(C(=O)C2=C(O)C(=O)N(c3cc(C)on3)C2c2cccc...               1   
11   C/C([NH2+]CCC[NH+]1CCOCC1)=C1/C(=O)NC(=O)N(c2c...               1   
12          CCC(CC)COC(=O)C(C#N)c1nc2ccccc2nc1N1CCOCC1               1   
13              CCc1nc(NCC[NH+]2CCOCC2)c2oc3ccccc3c2n1               1   
14     Cc1cc(-n2c(C)cc(C(=O)CSc3nnnn3-c3ccccc3)c2C)no1               1   
15   Cc1ccc(C)c(SCC(=O)OCC(=O)Nc2ccc(S(=O)(=O)N3CCO...               1   
16   Cc1ccc(-n2nnnc2SCC(=O)c2cc(C)n(-c3cc(C)on3)c2C...               1   
17   O=S(=O)(c1ccc2c(c1)OCCO2)N(Cc1ccc(F)cc1)Cc1nnc...               1   
18                CCN(C(=O)CSc1nc[nH]n1)c1cccc2ccccc12               1   
19      CN(Cc1ccccc1)C(=O)CSc1nc2ccccc2c(=O)n1Cc1ccco1               1   
20                O=c1oc2ccccc2c([O-])c1/C=N/Cc1ccccn1               1   
21   COC(=O)c1c(N)n(-c2ccc(N3CCOCC3)cc2)c2nc3ccccc3...               1   
22            O=C([O-])c1ccccc1C(=O)N1CCN(c2ccccc2)CC1               1   
23                     COc1cccc(Cn2c(=O)cnc3cncnc32)c1               1   
24     O=C(c1ccco1)N1CCC[C@@]2(CC[NH+](Cc3ccncc3)C2)C1               1   
25   COc1ccc(S(=O)(=O)N2CCC(C(=O)Nc3ccccc3C)CC2)c2c...               1   
26   CCOC(=O)N1CCN(C(=O)Nc2sc3nc4n(c(=O)c3c2C)CCC(C...               1   
27   O=C(CCS(=O)(=O)c1cccc2nsnc12)N1CCN(C(=O)c2ccco...               1   
28   CCOC(=O)Cn1c(=O)n(Cc2ccco2)c(=O)c2ccc(C(=O)NCC...               1   
29                  CSC1=[NH+]CCN1C(=O)c1ccc2c(c1)OCO2               1   
30   Cc1c(C(=O)N2CC[NH+](Cc3ccccc3)CC2)sc2ncnc(N3CC...               1   
31   CCCCCn1c(C[NH+]2CCN(c3cc(Cl)ccc3C)CC2)nc2c1c(=...               1   
32           O=C(Nc1nccs1)C1(S(=O)(=O)c2ccc(Cl)cc2)CC1               1   
33   CN(C(=O)c1ccccn1)C(C(=O)Nc1ccc2c(c1)OCCO2)c1cc...               1   
34                CSc1ccc(C(=O)C(C)(C)[NH+]2CCOCC2)cc1               1   
35            CCCn1c2ccccc2c2nnc(SCC(=O)Nc3ncccn3)nc21               1   
36      CC1(C)CC(=O)C2=C(C1)OC(c1cccs1)C(C#N)=C2[NH3+]               1   
37      COc1ccc(Nc2cc(=O)n(C3CCCCC3)c(=O)[nH]2)c(OC)c1               1   
38   O=C(CCNS(=O)(=O)c1cccc2nonc12)N1CCN(c2cccc(Cl)...               1   
39   O=C(C[NH+]1CCN(S(=O)(=O)c2cc(Cl)ccc2Cl)CC1)Nc1...               1   
40    COc1ccc(Br)cc1CNC(=O)C1CCN(S(=O)(=O)N2CCCCC2)CC1               1   
41   CC(=O)Nc1ccc(NC(=O)Cn2cnc3c(cnn3C(C)(C)C)c2=O)cc1               1   
42   CCOc1ccc(NC(=O)N(CC[NH+]2CCOCC2)Cc2ccc3c(c2)CC...               1   
43   COc1ccc(S(=O)(=O)N2CCC[NH+](CC(=O)Nc3ccc(OC)c(...               1   
44         CCCN1C(=O)C(O)(C2CC(=O)CC(C)(C)O2)c2ccccc21               1   
45   N#CC1=C(SCC(=O)NC23CC4CC(CC(C4)C2)C3)NC(=O)C(C...               1   
46                     O=C(CCNc1cc(Cl)cc(Cl)c1)c1ccco1               1   
47         CC(C)(C)c1cc(C[NH+](CCO)CCO)cc(C(C)(C)C)c1O               1   
48          O=C1CC(Sc2nnc(-c3ccccc3)o2)C(=O)N1c1ccccc1               1   
49                         COc1ccc(N/C=C2/CCCCC2=O)cc1               1   
50   CC(C)(C)c1ccc(S(=O)(=O)NCC(=O)N2CCN(C(=O)c3ccc...               1   
51            CC1=C(C(=O)Nc2ccccc2)C(c2cccs2)n2nnnc2N1               1   
52   CCOc1cc(C2C(C#N)=C([NH3+])SC([NH3+])=C2C#N)ccc...               1   
53   CS(=O)(=O)N(CC(=O)NCCSCc1c(F)cccc1Cl)c1ccc2c(c.

# Data scaling

In [16]:
#MinMax scaling because the data is not gaussian distributed
scaler = MinMaxScaler()

#dataframe to use
scaled_df = df_molecules
for column in descriptors:
    scaled_df[column] = pd.DataFrame(scaler.fit_transform(pd.DataFrame(df_molecules[column])),columns=[column])
scaled_df

SMILES ALDH1-inhibitor  \
0    COc1ccccc1CC(NC(C)=O)C(=O)NC1CCN(c2nnnn2-c2ccc...               1   
1               O=C(CSc1nc2cccnc2n1Cc1ccccc1)NCc1ccco1               1   
2    Cc1cccc2cc(C[NH+](CC3CCCO3)C(c3nnnn3Cc3ccco3)C...               1   
3                    CCN(CC)c1ccc2c(Cl)c(Br)c(=O)oc2c1               1   
4    CS(=O)(=O)N1CCc2cc(-c3csc(NC(=O)Cc4cccs4)n3)ccc21               1   
5    CC1CCCCN1S(=O)(=O)c1ccc(NC(=O)c2cccc(-n3cnnn3)...               1   
6         COCCN(C(=O)C(F)(F)F)C(C(=O)NC1CCCCC1)c1ccco1               1   
7        COc1ccccc1N1CCN(C(=O)CSc2nnc(-c3ccoc3C)o2)CC1               1   
8                 O=c1c2ccccc2nc(SCc2ccccc2)n1Cc1ccco1               1   
9             N#Cc1c(NC(=O)CSc2nnnn2C2CCCC2)sc2c1CCCC2               1   
10   COc1ccc(C(=O)C2=C(O)C(=O)N(c3cc(C)on3)C2c2cccc...               1   
11   C/C([NH2+]CCC[NH+]1CCOCC1)=C1/C(=O)NC(=O)N(c2c...               1   
12          CCC(CC)COC(=O)C(C#N)c1nc2ccccc2nc1N1CCOCC1               1   
13              CCc1nc(NCC[NH+]2CCOCC2)c2oc3ccccc3c2n1               1   
14     Cc1cc(-n2c(C)cc(C(=O)CSc3nnnn3-c3ccccc3)c2C)no1               1   
15   Cc1ccc(C)c(SCC(=O)OCC(=O)Nc2ccc(S(=O)(=O)N3CCO...               1   
16   Cc1ccc(-n2nnnc2SCC(=O)c2cc(C)n(-c3cc(C)on3)c2C...               1   
17   O=S(=O)(c1ccc2c(c1)OCCO2)N(Cc1ccc(F)cc1)Cc1nnc...               1   
18                CCN(C(=O)CSc1nc[nH]n1)c1cccc2ccccc12               1   
19      CN(Cc1ccccc1)C(=O)CSc1nc2ccccc2c(=O)n1Cc1ccco1               1   
20                O=c1oc2ccccc2c([O-])c1/C=N/Cc1ccccn1               1   
21   COC(=O)c1c(N)n(-c2ccc(N3CCOCC3)cc2)c2nc3ccccc3...               1   
22            O=C([O-])c1ccccc1C(=O)N1CCN(c2ccccc2)CC1               1   
23                     COc1cccc(Cn2c(=O)cnc3cncnc32)c1               1   
24     O=C(c1ccco1)N1CCC[C@@]2(CC[NH+](Cc3ccncc3)C2)C1               1   
25   COc1ccc(S(=O)(=O)N2CCC(C(=O)Nc3ccccc3C)CC2)c2c...               1   
26   CCOC(=O)N1CCN(C(=O)Nc2sc3nc4n(c(=O)c3c2C)CCC(C...               1   
27   O=C(CCS(=O)(=O)c1cccc2nsnc12)N1CCN(C(=O)c2ccco...               1   
28   CCOC(=O)Cn1c(=O)n(Cc2ccco2)c(=O)c2ccc(C(=O)NCC...               1   
29                  CSC1=[NH+]CCN1C(=O)c1ccc2c(c1)OCO2               1   
30   Cc1c(C(=O)N2CC[NH+](Cc3ccccc3)CC2)sc2ncnc(N3CC...               1   
31   CCCCCn1c(C[NH+]2CCN(c3cc(Cl)ccc3C)CC2)nc2c1c(=...               1   
32           O=C(Nc1nccs1)C1(S(=O)(=O)c2ccc(Cl)cc2)CC1               1   
33   CN(C(=O)c1ccccn1)C(C(=O)Nc1ccc2c(c1)OCCO2)c1cc...               1   
34                CSc1ccc(C(=O)C(C)(C)[NH+]2CCOCC2)cc1               1   
35            CCCn1c2ccccc2c2nnc(SCC(=O)Nc3ncccn3)nc21               1   
36      CC1(C)CC(=O)C2=C(C1)OC(c1cccs1)C(C#N)=C2[NH3+]               1   
37      COc1ccc(Nc2cc(=O)n(C3CCCCC3)c(=O)[nH]2)c(OC)c1               1   
38   O=C(CCNS(=O)(=O)c1cccc2nonc12)N1CCN(c2cccc(Cl)...               1   
39   O=C(C[NH+]1CCN(S(=O)(=O)c2cc(Cl)ccc2Cl)CC1)Nc1...               1   
40    COc1ccc(Br)cc1CNC(=O)C1CCN(S(=O)(=O)N2CCCCC2)CC1               1   
41   CC(=O)Nc1ccc(NC(=O)Cn2cnc3c(cnn3C(C)(C)C)c2=O)cc1               1   
42   CCOc1ccc(NC(=O)N(CC[NH+]2CCOCC2)Cc2ccc3c(c2)CC...               1   
43   COc1ccc(S(=O)(=O)N2CCC[NH+](CC(=O)Nc3ccc(OC)c(...               1   
44         CCCN1C(=O)C(O)(C2CC(=O)CC(C)(C)O2)c2ccccc21               1   
45   N#CC1=C(SCC(=O)NC23CC4CC(CC(C4)C2)C3)NC(=O)C(C...               1   
46                     O=C(CCNc1cc(Cl)cc(Cl)c1)c1ccco1               1   
47         CC(C)(C)c1cc(C[NH+](CCO)CCO)cc(C(C)(C)C)c1O               1   
48          O=C1CC(Sc2nnc(-c3ccccc3)o2)C(=O)N1c1ccccc1               1   
49                         COc1ccc(N/C=C2/CCCCC2=O)cc1               1   
50   CC(C)(C)c1ccc(S(=O)(=O)NCC(=O)N2CCN(C(=O)c3ccc...               1   
51            CC1=C(C(=O)Nc2ccccc2)C(c2cccs2)n2nnnc2N1               1   
52   CCOc1cc(C2C(C#N)=C([NH3+])SC([NH3+])=C2C#N)ccc...               1   
53   CS(=O)(=O)N(CC(=O)NCCSCc1c(F)cccc1Cl)c1ccc2c(c.

In [17]:
scaled_df_1 = scaled_df[scaled_df['ALDH1-inhibitor']=='1']
scaled_df_0 = scaled_df[scaled_df['ALDH1-inhibitor']=='0']
corr_df_1= scaled_df_1.copy()
corr_df_0=scaled_df_0.copy()

In [18]:
scaled_df.corr()

C:\Users\20213656\AppData\Local\Temp\ipykernel_11432\1902730301.py:1: FutureWarning: The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.
  scaled_df.corr()


MaxAbsEStateIndex  MinAbsEStateIndex  \
MaxAbsEStateIndex                  1.000000          -0.111562   
MinAbsEStateIndex                 -0.111562           1.000000   
MinEStateIndex                    -0.053491           0.068020   
qed                               -0.089767           0.084876   
MolWt                              0.562445          -0.213581   
NumRadicalElectrons                     NaN                NaN   
MaxPartialCharge                   0.014501          -0.000560   
MinPartialCharge                   0.072793          -0.008972   
FpDensityMorgan1                  -0.297042          -0.001419   
BCUT2D_MWHI                        0.061701          -0.066323   
BCUT2D_MWLOW                      -0.151790           0.087062   
BCUT2D_CHGHI                       0.403396          -0.193730   
BCUT2D_CHGLO                      -0.323483           0.121288   
BCUT2D_LOGPHI                      0.191793          -0.056407   
BCUT2D_LOGPLOW                    -0.278736           0.189541   
BCUT2D_MRHI                        0.078413          -0.082865   
BCUT2D_MRLOW                       0.128414           0.176107   
AvgIpc                             0.385645          -0.119183   
BalabanJ                          -0.298299           0.097947   
HallKierAlpha                     -0.359830           0.047280   
Ipc                                0.311926          -0.107658   
PEOE_VSA1                          0.037893          -0.004667   
PEOE_VSA10                         0.186423           0.004045   
PEOE_VSA11                         0.076738          -0.039087   
PEOE_VSA12                         0.122348          -0.124149   
PEOE_VSA13                         0.192262          -0.010746   
PEOE_VSA14                        -0.013737          -0.047616   
PEOE_VSA2                          0.196816          -0.139218   
PEOE_VSA3                          0.228667          -0.007256   
PEOE_VSA4                          0.047009          -0.039549   
PEOE_VSA5                          0.010712          -0.047011   
PEOE_VSA6                          0.137822          -0.031530   
PEOE_VSA7                          0.303566          -0.044892   
PEOE_VSA8                          0.169174          -0.090518   
PEOE_VSA9                          0.193484          -0.111614   
SMR_VSA1                           0.192287          -0.168145   
SMR_VSA10                          0.108666          -0.071338   
SMR_VSA2                                NaN                NaN   
SMR_VSA3                           0.151510          -0.032111   
SMR_VSA4                          -0.058202          -0.030027   
SMR_VSA5                           0.131047          -0.175805   
SMR_VSA6                           0.167982          -0.055978   
SMR_VSA7                           0.365378           0.018263   
SMR_VSA8                                NaN                NaN   
SMR_VSA9                           0.053615           0.016221   
SlogP_VSA1                         0.092756          -0.014850   
SlogP_VSA10                        0.123231           0.021653   
SlogP_VSA11                       -0.001768          -0.009510   
SlogP_VSA12                       -0.049548          -0.055490   
SlogP_VSA2                         0.224829          -0.172781   
SlogP_VSA3                         0.236958          -0.203161   
SlogP_VSA4                         0.067814          -0.062289   
SlogP_VSA7                              NaN                NaN   
SlogP_VSA8                         0.115262           0.023579   
SlogP_VSA9                              NaN                NaN   
TPSA                               0.144137          -0.140151   
EState_VSA1                        0.210274          -0.115943   
EState_VSA10                       0.259887          -0.253318   
EState_VSA11                            NaN                NaN   
EState_VSA2                        0.210439          -0.390610   


# PCA

In [19]:
from sklearn.decomposition import PCA
descriptors_with_ALDH1=descriptors
descriptors_with_ALDH1.insert(0,'ALDH1-inhibitor')
X=scaled_df[descriptors_with_ALDH1].values
X.shape

(1000, 85)

In [20]:
pca_85=PCA(n_components=85)
pca_85.fit(X)

ValueError: Input X contains NaN.
PCA does not accept missing values encoded as NaN natively. For supervised learning, you might want to consider sklearn.ensemble.HistGradientBoostingClassifier and Regressor which accept missing values encoded as NaNs natively. Alternatively, it is possible to preprocess the data, for instance by using an imputer transformer in a pipeline or drop samples with missing values. See https://scikit-learn.org/stable/modules/impute.html You can find a list of all estimators that handle NaN values at the following page: https://scikit-learn.org/stable/modules/impute.html#estimators-that-handle-nan-values